In [1]:
# read sdf file and extract SMILES using rdkit


from rdkit import Chem
from rdkit.Chem import AllChem


In [2]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
#import cosiine similarity from sklearn
from sklearn.metrics.pairwise import cosine_similarity
#import PCA from sklearn
from sklearn.decomposition import PCA


import ast  # For safely evaluating strings that represent lists


In [3]:

def convert_string_to_list(string):
    try:
        # Safely evaluate the string as a Python literal (list)
        return ast.literal_eval(string)
    except:
        # If the conversion fails, return the original value
        return string
fixed_df = pd.read_csv("fixed_df.csv")

print(fixed_df.columns)

fixed_df = fixed_df.map(convert_string_to_list)
fixed_df["CHEMBL"]= [False]*len(fixed_df)

def deduplicate_columns(df):
    deduplicated_df = pd.DataFrame()
    root_names = set(col.split('_x')[0] for col in df.columns if '_x' in col)

    for root in root_names:
        x_column = f'{root}_x'
        y_column = f'{root}_y'
        if x_column in df.columns:
            deduplicated_df[root] = df[x_column]
        elif y_column in df.columns:
            deduplicated_df[root] = df[y_column]

    # Add columns that do not have 'x' or 'y' variants
    for col in df.columns:
        if '_x' not in col and '_y' not in col and col not in deduplicated_df.columns:
            deduplicated_df[col] = df[col]

    return deduplicated_df

fixed_df = deduplicate_columns(fixed_df)





Index(['SMILES', 'r_concentration_uM_x', 'r_inhibition_list_x',
       'f_concentration_uM_x', 'f_inhibition_list_x', 'r_concentration_uM_y',
       'r_inhibition_list_y', 'f_concentration_uM_y', 'f_inhibition_list_y',
       'r_concentration_uM_x.1', 'r_inhibition_list_x.1',
       'f_concentration_uM_x.1', 'f_inhibition_list_x.1',
       'r_concentration_uM_y.1', 'r_inhibition_list_y.1',
       'f_concentration_uM_y.1', 'f_inhibition_list_y.1',
       'r_concentration_uM_x.1.1', 'r_inhibition_list_x.1.1',
       'f_concentration_uM_x.1.1', 'f_inhibition_list_x.1.1',
       'r_concentration_uM_y.1.1', 'r_inhibition_list_y.1.1',
       'f_concentration_uM_y.1.1', 'f_inhibition_list_y.1.1',
       'r_concentration_uM_x.1.1.1', 'r_inhibition_list_x.1.1.1',
       'f_concentration_uM_x.1.1.1', 'f_inhibition_list_x.1.1.1',
       'r_concentration_uM_y.1.1.1', 'r_inhibition_list_y.1.1.1',
       'f_concentration_uM_y.1.1.1', 'f_inhibition_list_y.1.1.1',
       'r_concentration_uM_x.1.1.1.1'

In [4]:
print(len(fixed_df))

# print number which have both f_avg_IC50 and r_avg_IC50
print(len(fixed_df[(fixed_df.f_avg_IC50.notnull()) & (fixed_df.r_avg_IC50.notnull())]))


# set Training = False for rows which have both f_avg_IC50 and r_avg_IC50 else set Training = True
fixed_df["Training"] = fixed_df.apply(lambda row: False if (pd.notnull(row["f_avg_IC50"]) and pd.notnull(row["r_avg_IC50"])) else True, axis=1)

#print percentage Training = False
print(len(fixed_df[fixed_df.Training == False])/len(fixed_df))


# create avg_IC50 from mean of f_avg_IC50 and r_avg_IC50 if both are not null otherwise use whichever is not null
fixed_df["avg_IC50"] = fixed_df.apply(lambda row: row["f_avg_IC50"] if pd.isnull(row["r_avg_IC50"]) else row["r_avg_IC50"] if pd.isnull(row["f_avg_IC50"]) else (row["f_avg_IC50"]+row["r_avg_IC50"])/2, axis=1)



2473
661
0.2672866963202588


In [5]:

# Path to SDF file of unlabelled ChemBL dataset
sdf_file = "FLuID_full.sdf"

# Read SDF file
supplier = Chem.SDMolSupplier(sdf_file)

# Convert each molecule to SMILES and store in a list
smiles_list = []
for mol in supplier:
    if mol is not None:  # Check if the molecule is valid
        smiles = Chem.MolToSmiles(mol)
        smiles_list.append(smiles)
        # chembl = True

chembl = [True]*len(smiles_list)


# create a padnas dataframe to store the smiles and chembl
df = pd.DataFrame(list(zip(smiles_list, chembl)),
               columns =['SMILES', 'CHEMBL'])

df = df.sample(5000) # may need to add more later

fixed_df = pd.concat([fixed_df, df])

# Printing the SMILES strings
print(len(smiles_list))




[00:54:32] WARNING: not removing hydrogen atom without neighbors
[00:54:32] WARNING: not removing hydrogen atom without neighbors
[00:54:32] Explicit valence for atom # 0 I, 6, is greater than permitted
[00:54:32] ERROR: Could not sanitize molecule ending on line 21889
[00:54:32] ERROR: Explicit valence for atom # 0 I, 6, is greater than permitted
[00:54:37] Explicit valence for atom # 0 Cl, 2, is greater than permitted
[00:54:37] ERROR: Could not sanitize molecule ending on line 1925660
[00:54:37] ERROR: Explicit valence for atom # 0 Cl, 2, is greater than permitted
[00:54:37] Explicit valence for atom # 0 Cl, 3, is greater than permitted
[00:54:37] ERROR: Could not sanitize molecule ending on line 1925733
[00:54:37] ERROR: Explicit valence for atom # 0 Cl, 3, is greater than permitted
[00:54:37] Explicit valence for atom # 0 Cl, 7, is greater than permitted
[00:54:37] ERROR: Could not sanitize molecule ending on line 1925823
[00:54:37] ERROR: Explicit valence for atom # 0 Cl, 7, is g

347717


In [10]:
ECFPS = []
FCFPS = []
ESTATE2 = []
MACCS = []
FP2 = []
DAYLIGHT = []

# from openbabel import pybel


# Generate ECFP4 and FCFP fingerprints for each molecule from SMILES in df
for smiles in fixed_df['SMILES']:
    mol = Chem.MolFromSmiles(smiles)
    ecfp = AllChem.GetMorganFingerprintAsBitVect(mol, 2, nBits=1024)
    fcfp = AllChem.GetMorganFingerprintAsBitVect(mol, 2, useFeatures=True, nBits=1024)
    ECFPS.append(ecfp)
    FCFPS.append(fcfp)
    estate2 = AllChem.GetHashedAtomPairFingerprintAsBitVect(mol)
    ESTATE2.append(estate2)
    maccs = AllChem.GetMACCSKeysFingerprint(mol)
    MACCS.append(maccs)
    # FP2 from openbabel
    # ob_mol = pybel.readstring("smi", smiles)
    # fp2 = ob_mol.calcfp("FP2")
    # FP2.append(fp2.fp)
    # daylight from rdkit
    daylight = Chem.RDKFingerprint(mol)
    DAYLIGHT.append(daylight)



fixed_df['ECFP'] = ECFPS
fixed_df['FCFP'] = FCFPS
fixed_df['ESTATE2'] = ESTATE2
fixed_df['MACCS'] = MACCS
# fixed_df['FP2'] = FP2
fixed_df['DAYLIGHT'] = DAYLIGHT


fixed_df["multi"]  = fixed_df.apply(lambda row: row["ECFP"]+row["FCFP"]+row["ESTATE2"]+row["MACCS"]+row["DAYLIGHT"], axis=1)



In [9]:
# concatenate all the fingerprints per row

def do_PCA_df(df: pd.DataFrame, fps: list[str], cosine=True) -> pd.DataFrame:
    for fp_col in fps:

        PC_cols = ["PC1", "PC2"]
        PC_cols = [fp_col + "_" + col for col in PC_cols]

        FPs= df[fp_col].tolist()

        matrix = np.array(FPs)
        if cosine:
            matrix = cosine_similarity(FPs)
        pca = PCA(n_components=2)
        pca.fit(matrix)
        X = pca.transform(matrix)

        df[PC_cols[0]] = X[:, 0]
        df[PC_cols[1]] = X[:, 1]

    return df


fixed_df = do_PCA_df(fixed_df, ["ECFP", "FCFP", "multi"], cosine=True)



In [11]:
print(len(fixed_df.avg_IC50.dropna()))

2473


In [12]:
# plot FCFP PCA

fig = px.scatter(fixed_df, x="ECFP_PC1", y="ECFP_PC2", color="Training", hover_data=['SMILES'],opacity=0.5)
fig.show()

In [13]:
# plot FCFP PCA

fig = px.scatter(fixed_df, x="FCFP_PC1", y="FCFP_PC2", color="Training", hover_data=['SMILES'],opacity=0.5)
fig.show()

In [14]:

fig = px.scatter(fixed_df, x="multi_PC1", y="multi_PC2", color="Training", hover_data=['SMILES'],opacity=0.5)
fig.show()

In [15]:
# select data that are <96 for both f_avg_IC50 and r_avg_IC50
clean_df = fixed_df[(fixed_df.f_avg_IC50 < 96) & (fixed_df.r_avg_IC50 < 96)]
print(len(clean_df))

# plot FCFP PCA

fig = px.scatter(clean_df, x="FCFP_PC1", y="FCFP_PC2", color="avg_IC50", hover_data=['SMILES'],opacity=0.5)
fig.show()
 


420


In [16]:
# sample evenly across FCFP_PC1 and FCFP_PC2 - select 200 in total

# Number of bins for each dimension
n_bins = 30

# Create bins for each dimension
clean_df['FCFP_PC1_bin'] = pd.qcut(clean_df['FCFP_PC1'], n_bins, labels=False, duplicates='drop')
clean_df['FCFP_PC2_bin'] = pd.qcut(clean_df['FCFP_PC2'], n_bins, labels=False, duplicates='drop')

# Group by the bins and sample
sampled_df = clean_df.groupby(['FCFP_PC1_bin', 'FCFP_PC2_bin']).sample(n=1, random_state=1)

# If the number of bins squared is greater than 200, sample down to 200
if len(sampled_df) > 200:
    sampled_df = sampled_df.sample(n=200, random_state=1)

print(f"Number of points in sampled data: {len(sampled_df)}")

# Plot histogram of the sampled data for avg_IC50 compare sampled df to clean df on the same plot

# Create histograms for both datasets
hist_clean = go.Histogram(
    x=clean_df['avg_IC50'], 
    name='Clean Data', 
    opacity=0.75, 
    marker=dict(color='blue'),
    histnorm='probability'  # Normalize to show relative frequency

)

hist_sampled = go.Histogram(
    x=sampled_df['avg_IC50'], 
    name='Sampled Data', 
    opacity=0.75, 
    marker=dict(color='red'),
    histnorm='probability'  # Normalize to show relative frequency

)

# Create a figure and add both histograms
fig = go.Figure()
fig.add_trace(hist_clean)
fig.add_trace(hist_sampled)

# Update layout
fig.update_layout(
    title='Comparison of avg_IC50 Distribution: Clean vs Sampled Data',
    xaxis_title='avg_IC50',
    yaxis_title='Count',
    barmode='overlay'
)

# Show the plot
fig.show()

test_df = sampled_df.copy()

Number of points in sampled data: 200


/var/folders/4c/64jkr7n54w1558kqk0ks5rgr0000gn/T/ipykernel_69855/3729593463.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/4c/64jkr7n54w1558kqk0ks5rgr0000gn/T/ipykernel_69855/3729593463.py:8: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [17]:
# sample 20 of f_avg_IC50 >96 and r_avg_IC50 is null
sample_f = fixed_df[(fixed_df.f_avg_IC50 > 96) & (fixed_df.r_avg_IC50.isnull())].sample(10)
# sample 20 of r_avg_IC50 >96 and f_avg_IC50 is null 
sample_r = fixed_df[(fixed_df.r_avg_IC50 > 96) & (fixed_df.f_avg_IC50.isnull())].sample(10)

sample_both = fixed_df[(fixed_df.r_avg_IC50 > 96) & (fixed_df.f_avg_IC50 > 96)].sample(10)

test_df = pd.concat([test_df, sample_f, sample_r, sample_both])


# sample 20 of f_avg_IC50 >96 and r_avg_IC50 is null
sample_f = fixed_df[(fixed_df.f_avg_IC50 > 96) & (fixed_df.r_avg_IC50 < 96 )].sample(10)
# sample 20 of r_avg_IC50 >96 and f_avg_IC50 is null 
sample_r = fixed_df[(fixed_df.r_avg_IC50 > 96) & (fixed_df.f_avg_IC50 < 96 )].sample(10)

test_df = pd.concat([test_df, sample_f, sample_r])

# sample 10 where both f_avg_IC50 and r_avg_IC50 are >  

# concat the 3 samples to test_df


# # drop duplicates SMILES
# test_df = test_df.drop_duplicates(subset=['SMILES'])
print(len(test_df))
test_df = test_df.drop_duplicates(subset=['SMILES'])
print(len(test_df))

250
249


In [18]:

# Create histograms for both datasets
hist_clean = go.Histogram(
    x=fixed_df['avg_IC50'], 
    name='Clean Data', 
    opacity=0.75, 
    marker=dict(color='blue'),
    nbinsx=25,
    histnorm='probability'  # Normalize to show relative frequency

)

hist_sampled = go.Histogram(
    x=test_df['avg_IC50'], 
    name='Sampled Data', 
    opacity=0.75, 
    marker=dict(color='red'),
    nbinsx=25,
    histnorm='probability'  # Normalize to show relative frequency

)

# Create a figure and add both histograms
fig = go.Figure()
fig.add_trace(hist_clean)
fig.add_trace(hist_sampled)

# Update layout
fig.update_layout(
    title='Comparison of avg_IC50 Distribution: Clean vs Sampled Data',
    xaxis_title='avg_IC50',
    yaxis_title='Count',
    barmode='overlay'
)

# Show the plot
fig.show()


In [19]:
import plotly.express as px
import plotly.graph_objects as go

# Create initial scatter plot for clean_df
fig = px.scatter(
    fixed_df, 
    x="FCFP_PC1", 
    y="FCFP_PC2", 
    color="avg_IC50", 
    hover_data=['SMILES'], 
    opacity=0.1,
    title='FCFP_PC1 vs FCFP_PC2: Clean and Sampled Data'
)

# Add sampled_df as a second trace
fig.add_trace(
    go.Scatter(
        x=sampled_df["FCFP_PC1"], 
        y=sampled_df["FCFP_PC2"], 
        mode='markers',
        marker=dict(
            color='rgba(0, 255, 0, 0.5)',  # Green color with 50% opacity
            size=10
        ),
        name='Sampled Data',
        hoverinfo='text',
        hovertext=sampled_df['SMILES']
    )
)

# Update layout if needed
fig.update_layout(
    xaxis_title='FCFP_PC1',
    yaxis_title='FCFP_PC2'
)

# Show the plot
fig.show()

print(len(sampled_df))
print(len(clean_df))


200
420


In [20]:
import plotly.express as px
import plotly.graph_objects as go

# Create initial scatter plot for clean_df
fig = px.scatter(
    fixed_df, 
    x="ECFP_PC1", 
    y="ECFP_PC2", 
    color="avg_IC50", 
    hover_data=['SMILES'], 
    opacity=0.1,
    title='ECFP_PC1 vs ECFP_PC2: Clean and Sampled Data'
)

# Add sampled_df as a second trace
fig.add_trace(
    go.Scatter(
        x=sampled_df["ECFP_PC1"], 
        y=sampled_df["ECFP_PC2"], 
        mode='markers',
        marker=dict(
            color='rgba(0, 255, 0, 0.5)',  # Green color with 50% opacity
            size=10
        ),
        name='Sampled Data',
        hoverinfo='text',
        hovertext=sampled_df['SMILES']
    )
)

# Update layout if needed
fig.update_layout(
    xaxis_title='ECFP_PC1',
    yaxis_title='ECFP_PC2'
)

# Show the plot
fig.show()

print(len(sampled_df))
print(len(clean_df))


200
420


In [21]:
import plotly.express as px
import plotly.graph_objects as go

# Create initial scatter plot for clean_df
fig = px.scatter(
    fixed_df, 
    x="multi_PC1", 
    y="multi_PC2", 
    color="avg_IC50", 
    hover_data=['SMILES'], 
    opacity=0.1,
    title='multi_PC1 vs multi_PC2: Fixed and test_df Data'
)

# Add sampled_df as a second trace
fig.add_trace(
    go.Scatter(
        x=test_df["multi_PC1"], 
        y=test_df["multi_PC2"], 
        mode='markers',
        marker=dict(
            color='rgba(0, 255, 0, 0.5)',  # Green color with 50% opacity
            size=10
        ),
        name='Sampled Data',
        hoverinfo='text',
        hovertext=sampled_df['SMILES']
    )
)

# Update layout if needed
fig.update_layout(
    xaxis_title='multi_PC1',
    yaxis_title='multi_PC2'
)

# Show the plot
fig.show()

print(len(test_df))
print(len(clean_df))


249
420


In [22]:
# drop columns with fingerprints
columns_to_drop = ['ECFP', 'FCFP', 'ESTATE2', 'MACCS', 'DAYLIGHT', 'multi', 'ECFP_PC1', 'ECFP_PC2', 'FCFP_PC1', 'FCFP_PC2', 'multi_PC1', 'multi_PC2']
fixed_df = fixed_df.drop(columns_to_drop, axis=1)
test_df = test_df.drop(columns_to_drop, axis=1)


In [23]:
# create df with test df removed and  remove CHEMBL = True
rest_df = fixed_df[~fixed_df.SMILES.isin(test_df.SMILES)]
rest_df = rest_df[rest_df.CHEMBL == False]



print(len(rest_df))

2124


In [24]:
# save test_df to csv
test_df.to_csv("FCFP_bin30_testset_df.csv", index=False)

# save rest_df to csv
rest_df.to_csv("FCFP_bin30_rest_df.csv", index=False)

In [25]:
# save test_df to pkl
test_df.to_pickle("FCFP_bin30_testset_df.pkl")

test_df.to_csv("FCFP_bin30_testset_df.csv", index=False)

# save rest_df to pkl
rest_df.to_pickle("FCFP_bin30_rest_df.pkl")

In [26]:
train_df = rest_df.sample(frac=0.9, random_state=1)
val_df = rest_df.drop(train_df.index)

# save train_df to pkl
train_df.to_pickle("FCFP_bin30_train_df.pkl")

# save val_df to pkl
val_df.to_pickle("FCFP_bin30_val_df.pkl")


In [27]:
# also save to csv
train_df.to_csv("FCFP_bin30_train_df.csv", index=False)
val_df.to_csv("FCFP_bin30_val_df.csv", index=False)
